# Baltic Sea Drift -- Preparation

We'll download a subset of the [Baltic Sea Physics Analysis and Forecast dataset](https://data.marine.copernicus.eu/product/BALTICSEA_ANALYSISFORECAST_PHY_003_006/description) dataset which only covers a few days at 3 hour resolution.

In [1]:
import copernicusmarine
import xarray as xr

/miniconda3/envs/jupyter/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
copernicusmarine.login()

INFO - 2025-06-28T15:56:04Z - Downloading Copernicus Marine data requires a Copernicus Marine username and password, sign up for free at: https://data.marine.copernicus.eu/register


Copernicus Marine username:

  wrath1


Copernicus Marine password:

  ········


INFO - 2025-06-28T15:56:17Z - Credentials file stored in /home/jovyan/.copernicusmarine/.copernicusmarine-credentials.


True

In [3]:
ds = copernicusmarine.open_dataset(dataset_id="cmems_mod_bal_phy_anfc_PT1H-i")
ds

INFO - 2025-06-28T15:56:19Z - Selected dataset version: "202411"
INFO - 2025-06-28T15:56:19Z - Selected dataset part: "default"


<xarray.Dataset> Size: 15TB
Dimensions:    (depth: 56, latitude: 774, longitude: 763, time: 22668)
Coordinates:
  * depth      (depth) float32 224B 0.5016 1.516 2.548 ... 663.9 688.0 712.0
  * latitude   (latitude) float32 3kB 53.01 53.02 53.04 ... 65.86 65.87 65.89
  * longitude  (longitude) float32 3kB 9.042 9.069 9.097 ... 30.15 30.18 30.21
  * time       (time) datetime64[ns] 181kB 2022-12-02T13:00:00 ... 2025-07-04
Data variables:
    bottomT    (time, latitude, longitude) float32 54GB dask.array<chunksize=(2, 774, 763), meta=np.ndarray>
    mlotst     (time, latitude, longitude) float32 54GB dask.array<chunksize=(2, 774, 763), meta=np.ndarray>
    siconc     (time, latitude, longitude) float32 54GB dask.array<chunksize=(2, 774, 763), meta=np.ndarray>
    sithick    (time, latitude, longitude) float32 54GB dask.array<chunksize=(2, 774, 763), meta=np.ndarray>
    sla        (time, latitude, longitude) float32 54GB dask.array<chunksize=(2, 774, 763), meta=np.ndarray>
    so         (time, depth, latitude, longitude) float32 3TB dask.array<chunksize=(2, 56, 774, 763), meta=np.ndarray>
    sob        (time, latitude, longitude) float32 54GB dask.array<chunksize=(2, 774, 763), meta=np.ndarray>
    thetao     (time, depth, latitude, longitude) float32 3TB dask.array<chunksize=(2, 56, 774, 763), meta=np.ndarray>
    uo         (time, depth, latitude, longitude) float32 3TB dask.array<chunksize=(2, 56, 774, 763), meta=np.ndarray>
    vo         (time, depth, latitude, longitude) float32 3TB dask.array<chunksize=(2, 56, 774, 763), meta=np.ndarray>
    wo         (time, depth, latitude, longitude) float32 3TB dask.array<chunksize=(2, 56, 774, 763), meta=np.ndarray>
Attributes:
    references:   https://marine.copernicus.eu/
    comment:      Data on cropped native product grid. Horizontal velocities ...
    title:        CMEMS NEMO hourly model fields
    contact:      servicedesk.cmems@mercator-ocean.eu
    source:       CMEMS BAL MFC NEMO model output converted to NetCDF
    Conventions:  CF-1.0
    institution:  Baltic MFC, PU Swedish Meteorological and Hydrological Inst...

In [4]:
ds_uv = (
    ds
    [["uo", "vo"]]
    .sel(time=slice("2023-01-01T00:00:00", "2023-01-10T00:00:00"))
    .isel(time=slice(None, None, 3))
    .sel(depth=5, method="nearest")
    .rename({"uo": "u", "vo": "v"})
)
ds_uv

<xarray.Dataset> Size: 345MB
Dimensions:    (time: 73, latitude: 774, longitude: 763)
Coordinates:
    depth      float32 4B 4.684
  * latitude   (latitude) float32 3kB 53.01 53.02 53.04 ... 65.86 65.87 65.89
  * longitude  (longitude) float32 3kB 9.042 9.069 9.097 ... 30.15 30.18 30.21
  * time       (time) datetime64[ns] 584B 2023-01-01 ... 2023-01-10
Data variables:
    u          (time, latitude, longitude) float32 172MB dask.array<chunksize=(1, 774, 763), meta=np.ndarray>
    v          (time, latitude, longitude) float32 172MB dask.array<chunksize=(1, 774, 763), meta=np.ndarray>
Attributes:
    references:   https://marine.copernicus.eu/
    comment:      Data on cropped native product grid. Horizontal velocities ...
    title:        CMEMS NEMO hourly model fields
    contact:      servicedesk.cmems@mercator-ocean.eu
    source:       CMEMS BAL MFC NEMO model output converted to NetCDF
    Conventions:  CF-1.0
    institution:  Baltic MFC, PU Swedish Meteorological and Hydrological Inst...

In [5]:
ds_uv.nbytes / 1e6

344.894944

In [6]:
%%time

ds_uv = ds_uv.compute()

CPU times: user 2min 44s, sys: 19.8 s, total: 3min 4s
Wall time: 4min 48s


In [7]:
!mkdir -p /home/jovyan/shared_materials/projects_data/

In [8]:
ds_uv.drop_encoding().to_netcdf("/home/jovyan/shared_materials/projects_data/01_baltic_sea_particle_drift_flow.nc")
ds_uv = xr.open_dataset("/home/jovyan/shared_materials/projects_data/01_baltic_sea_particle_drift_flow.nc")
ds_uv

<xarray.Dataset> Size: 345MB
Dimensions:    (time: 73, latitude: 774, longitude: 763)
Coordinates:
    depth      float32 4B ...
  * latitude   (latitude) float32 3kB 53.01 53.02 53.04 ... 65.86 65.87 65.89
  * longitude  (longitude) float32 3kB 9.042 9.069 9.097 ... 30.15 30.18 30.21
  * time       (time) datetime64[ns] 584B 2023-01-01 ... 2023-01-10
Data variables:
    u          (time, latitude, longitude) float32 172MB ...
    v          (time, latitude, longitude) float32 172MB ...
Attributes:
    references:   https://marine.copernicus.eu/
    comment:      Data on cropped native product grid. Horizontal velocities ...
    title:        CMEMS NEMO hourly model fields
    contact:      servicedesk.cmems@mercator-ocean.eu
    source:       CMEMS BAL MFC NEMO model output converted to NetCDF
    Conventions:  CF-1.0
    institution:  Baltic MFC, PU Swedish Meteorological and Hydrological Inst...

In [9]:
!ls -lah /home/jovyan/shared_materials/projects_data/01_baltic_sea_particle_drift_flow.nc

-rw-r--r-- 1 jovyan jovyan 329M Jun 28 18:01 /home/jovyan/shared_materials/projects_data/01_baltic_sea_particle_drift_flow.nc
